# T2D benchmark

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2
import os
os.chdir('../../')

In [2]:
import takco
conf = takco.Config('resources/config-dbpedia.toml')
t2dv2 = takco.TableSet.dataset('t2d-v2', **conf)

takco.preview(t2dv2)

In [3]:
%%time
import takco.link

kbs = {k.get("name", k.get("class")): takco.Config(k) for k in conf['kbs']}
# searcher_config = takco.Config({'name': 'dbpedialookup_t2ksubset'}, **kbs)
searcher_config = takco.Config({'name': 'dbpedia_t2ksubset_extralabels'}, **kbs)

pred = takco.TableSet.link(
    takco.HashBag(list(t2dv2)[:5]),
    usecols = "keycol",
    lookup_config = None,
    linker_config = takco.Config({
        "class": "First",
        "search_limit": 25,
        "searcher": searcher_config,
        "majority_class": "http://www.w3.org/1999/02/22-rdf-syntax-ns#type",
    }),
)
scored = takco.TableSet.score(pred, labels='t2d-v2', **conf)

report = takco.TableSet.report( scored, keycol_only=True )
report

CPU times: user 5.16 s, sys: 817 ms, total: 5.97 s
Wall time: 6.01 s


{'scores': {'entities': {'precision': 0.9283276450511946,
   'recall': 0.7148488830486203,
   'f1-score': 0.8077208611729769,
   'support': 761,
   'predictions': 586},
  'classes': {'precision': 1.0,
   'recall': 1.0,
   'f1-score': 1.0,
   'support': 5,
   'predictions': 5}}}

In [4]:
from rdflib import RDF, RDFS, URIRef
from takco.link import *
search = takco.Config(searcher_config).init_class(**globals())
search.exact = False

txt = "Jack"

results = search.search_entities(txt, limit=1000, add_about=True)

print(len(results))
for i, sr in enumerate(results):
    types = sr.get(RDF.type) or []
    if URIRef('http://dbpedia.org/ontology/Book') in types:
        print(i, sr.uri, sr.score, types, [str(l) for l in sr.get(RDFS.label)])

16
1 http://dbpedia.org/resource/Jack,_Knave_and_Fool 0.8571428571428572 [rdflib.term.URIRef('http://dbpedia.org/ontology/Book')] ['Jack Knave and Fool', 'Jack', 'Jack, Knave and Fool']
7 http://dbpedia.org/resource/Jack,_the_Giant_Killer 0.8 [rdflib.term.URIRef('http://dbpedia.org/ontology/Book')] ['Jack the Giant Killer', 'Jack', 'Jack, the Giant Killer']
15 http://dbpedia.org/resource/Jack_(novel) 0.8 [rdflib.term.URIRef('http://dbpedia.org/ontology/Book')] ['Jack (novel)', 'Jack']


In [5]:
takco.preview( scored, nrows=None, hide_correct_rows=True )

In [10]:
!time takco run -v -C resources/config-dbpedia.toml resources/pipelines/t2d-v2-baseline.toml

INFO:root:Set log level to 20
INFO:root:Loaded config {'name': 'config-dbpedia', 'datadir': 'data', 'resourcedir': 'resources', 'cache': False, 'kbs': [{'name': 'dbpedia_t2ksubset', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia_t2ksubset/db/'}}, {'name': 'dbpedia_2014_part2', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia/2014_part2/'}}, {'name': 'dbpedia_2016', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia/2016-10/'}}, {'name': 'dbpedialookup', 'class': 'DBpediaLookup'}], 'assets': [{'name': 't2d-v1', 'class': 'T2D', 'download': ['http://webdatacommons.org/webtables/tables_instance.tar.gz', 'http://webdatacommons.org/webtables/entities_instance.tar.gz', 'http://webdatacommons.org/webtables/classes_instance